# WebSocket API MRN Example with Python - RTO Connection (Authentication Version 1 )

**Last Update**: May 2024

Special thanks to Neeranat Junsuriyawong from the Solutions Consultant team for the contribution to this RTO notebook example.

## Prerequisite

This article/notebook is focusing on the LSEG Machine Readable News (MRN) data processing only. I highly recommend you check the  [WebSocket API Tutorials](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/refinitiv-websocket-api/tutorials) page if you are not familiar with WebSocket API. 

The Tutorials page provides a step-by-step guide (connect, log in, request data, parse data, etc) for developers who are interested in developing a WebSocket application to consume real-time news data from the Real-Time - Optimized (RTO) using the Authentication Version 1. 

If you are using the deployed the Real-Time Distribution System (RTDS), please check the [mrn_notebook_app_rtds.ipynb](./mrn_notebook_app_rtds.ipynb) notebook file.

Please contact your LSEG representative to help you to access the RTO account, and services. You can find more detail regarding the RTO access credentials set up from the *Getting Started for Machine ID* section of the [Getting Start with Refinitiv Data Platform article](https://developers.refinitiv.com/en/article-catalog/article/getting-start-with-refinitiv-data-platform) article.

## Machine Readable News Overview

The Machine Readable News (MRN) is an advanced service for automating the consumption and systematic analysis of news. It delivers deep historical news archives, ultra-low latency structured news and news analytics directly to your applications. This enables algorithms to exploit the power of news to seize opportunities, capitalize on market inefficiencies and manage event risk.

MRN aims for replacing the legacy News 2K (N2_UBMS and N2_STORY).

### MRN Data behavior

MRN is published over the Real-Time Platform using an Open Message Model (OMM) envelope in News Text Analytics domain messages. The Real-time News content set is made available over MRN_STORY RIC. The content data is contained in a FRAGMENT field that has been compressed, and potentially fragmented across multiple messages, in order to reduce bandwidth and message size.

A FRAGMENT field has a different data type based on a connection type:
* RSSL connection (ESDK [C++](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/rt-sdk-cc)/[Java](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/rt-sdk-java)/[C#](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/refinitiv-real-time-csharp-sdk): BUFFER type
* WebSocket connection: Base64 ascii string

The data goes through the following series of transformations:

1. The core content data is a UTF-8 JSON string
2. This JSON string is compressed using gzip
3. The compressed JSON is split into a number of fragments (BUFFER or Base64 ascii string) which each fit into a single update message
4. The data fragments are added to an update message as the FRAGMENT field value in a FieldList envelope


<img src="images/mrn_process.png"/>

Therefore, in order to parse the core content data, the application will need to reverse this process. The WebSocket application also need to convert a received Base64 string in a FRAGMENT field to bytes data before further process this field.

### MRN Data model

Five fields, as well as the RIC itself, are necessary to determine whether the entire item has been received in its various fragments and how to concatenate the fragments to reconstruct the item:
* MRN_SRC: identifier of the scoring/processing system that published the FRAGMENT
* GUID: a globally unique identifier for the data item. All messages for this data item will have the same GUID values.
* FRAGMENT: compressed data item fragment, itself
* TOT_SIZE: total size in bytes of the fragmented data
* FRAG_NUM: sequence number of fragments within a data item. This is set to 1 for the first fragment of each item published and is incremented for each subsequent fragment for the same item.

A single MRN data item publication is uniquely identified by the combination of RIC, MRN_SRC, and GUID.

#### Fragmentation
For a given RIC-MRN_SRC-GUID combination, when a data item requires only a single message, then TOT_SIZE will equal the number of bytes in the FRAGMENT and FRAG_NUM will be 1.

When multiple messages are required, then the data item can be deemed as fully received once the sum of the number of bytes of each FRAGMENT equals TOT_SUM. The consumer will also observe that all FRAG_NUM range from 1 to the number of the fragment, with no intermediate integers skipped. In other words, a data item transmitted over three messages will contain FRAG_NUM values of 1, 2 and 3.

#### Compression
The FRAGMENT field is compressed with gzip compression, thus requiring the consumer to decompress to reveal the JSON plain-text data in that FID.

When an MRN data item is sent in multiple messages, all the messages must be received and their FRAGMENTs concatenated before being decompressed. In other words, the FRAGMENTs should not be decompressed independently of each other.

The decompressed output is encoded in UTF-8 and formatted as JSON.

Please see a full documentation of this example application in [this article](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).

If you are not familiar with MRN concept, please visit the following resources which will give you a full explanation of the MRN data model and implementation logic:
* [Webinar Recording: Introduction to Machine Readable News](https://developers.lseg.com/news#news-accordion-nid-12045)
* [Introduction to Machine Readable News (MRN) with Enterprise Message API (EMA)](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-mrn-elektron-message-api-ema).
* [MRN Data Models and Refinitiv Real-Time Implementation Guide](https://developers.lseg.com/en/api-catalog/elektron/elektron-sdk-java/documentation#mrn-data-models-implementation-guide).
* [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.lseg.com/en/article-catalog/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).
* [Introduction to Machine Readable News with WebSocket API](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).
* [How to get MRN News Analytics Data via WebSocket API](https://developers.lseg.com/en/article-catalog/article/how-to-get-mrn-news-analytics-data-via-elektron-websocket-api).

In [1]:
# #uncomment if you do not have requests and websocket-client (version 0.49 and above) installed\n
# #Install requests and websocket-client packages in a current Jupyter kernal\n

import sys

# !{sys.executable} -m pip install requests
# !{sys.executable} -m pip install websocket-client
# !{sys.executable} -m pip install python-dotenv

In [2]:
import time
import getopt
import socket
import json
import websocket
import threading
from threading import Thread, Event
import base64
import zlib
import requests
import os
from dotenv import load_dotenv
import datetime

%load_ext dotenv

# Use find_dotenv to locate the file
%dotenv

You should save a text file with **filename** `.env` or OS Environment Variables having the following configurations:

```
# RTO Credentials
RTO_USERNAME=Machine-ID
RTO_PASSWORD=RTO-Password
RTO_CLIENTID=App-Key

# RDP-RTO Core Configurations
RDP_BASE_URL=https://api.refinitiv.com
RDP_AUTH_URL=/auth/oauth2/v1/token
RDP_DISCOVERY_URL=/streaming/pricing/v1/
```

In [3]:
os.getenv('RDP_BASE_URL')

'https://api.refinitiv.com'

### <a id="whatis_rdp"></a>What is Delivery Platform (RDP) APIs?

The [Delivery Platform (RDP) APIs](https://developers.refinitiv.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis) (previously known as Refinitiv Data Platform) provide various LSEG data and content for developers via easy to use Web-based API.

RDP APIs give developers seamless and holistic access to all of the Refinitiv content such as Historical Pricing, Environmental Social and Governance (ESG), News, Research, etc and commingled with their content, enriching, integrating, and distributing the data through a single interface, delivered wherever they need it. 

The RTO utilizes RDP APIs authentication and service discovery services. For more detail regarding the Delivery Platform, please see the following APIs resources: 
- [Quick Start](https://developers.lseg.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis/quick-start) page.
- [Tutorials](https://developers.lseg.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis/tutorials) page.
- [RDP APIs: Introduction to the Request-Response API](https://developers.lseg.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis/tutorials#introduction-to-the-request-response-api) page.
- [RDP APIs: Authorization - All about tokens](https://developers.lseg.com/en/api-catalog/refinitiv-data-platform/refinitiv-data-platform-apis/tutorials#authorization-all-about-tokens) page.

### <a id="whatis_rto"></a>What is Refinitiv Real-Time - Optimized?

As part of the Delivery Platform, [the Real-Time - Optimized](https://developers.lseg.com/en/api-catalog/elektron/refinitiv-websocket-api/quick-start#connecting-to-refinitiv-real-time-optimized) (RTO - formerly known as ERT in Cloud) gives you access to best in class Real-Time market data delivered in the cloud.  The Real-Time - Optimized is a new delivery mechanism for RDP, using the AWS (Amazon Web Services) cloud. Once a connection to RDP is established using RTO, data can be retrieved using [Websocket API for Pricing Streaming and Real-Time Services](https://developers.refinitiv.com/en/api-catalog/elektron/refinitiv-websocket-api) aka WebSocket API.

For more detail regarding the Real-Time - Optimized, please see the following APIs resources: 
- [WebSocket API Quick Start](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/refinitiv-websocket-api/quick-start#connecting-to-refinitiv-real-time-optimized) page.
- [WebSocket API Tutorials](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/refinitiv-websocket-api/tutorials#connect-to-refinitiv-real-time-optimized) page.
- [How to Setup Refinitiv's Amazon EC2 Machine Image for the Real-Time - Optimized](https://developers.lseg.com/en/article-catalog/article/how-to-setup-refinitiv-amazon-ec2-machine-image-for-elektron-r) article.

#### RDP and RTO Endpoints

The RTO application needs to get authentication information from the RDP Auth Service. The application can get the Real-Time service endpoints dynamically from the RDP Service Discovery service.

In [4]:
base_url = os.getenv('RDP_BASE_URL')
auth_url = base_url +  os.getenv('RDP_AUTH_URL');
discovery_url = base_url +  os.getenv('RDP_DISCOVERY_URL');

#### RTO Credentials

The Real-Time - Optimized (RTO) Authentication Version 1 needs the following access credentials:
- Machine-ID
- RTO Password
- ClientID (aka AppKey)


In [9]:
user= os.getenv('RTO_USERNAME') 
clientid= os.getenv('RTO_CLIENTID') 
password= os.getenv('RTO_PASSWORD') 

# RTO variables
sts_token = ''
refresh_token = ''
original_expire_time = '0'
expire_time = '0'
client_secret = ''
scope = 'trapi.streaming.pricing.read'
region = 'us-east-1'
service = 'ELEKTRON_DD'

In [10]:
# Refinitiv Real-Time Advanced Distribution Server connection variables
hostList = []
port = '15000'
app_id = '256'
position = socket.gethostbyname(socket.gethostname())
login_id = 1

In [11]:
# WebSocket connections Variables

web_socket_app = None
web_socket_open = False
_news_envelopes = []

# keeps decompress news JSON messaage
_news_messages = []

### RDP Token retrival

In order to connect to RTO, you need to retrieve token from the Token API first. This part of the code will take care of then token retrieval for you.

In [12]:
def get_sts_token(current_refresh_token, url=None):
    """
        Retrieves an authentication token.
        :param current_refresh_token: Refresh token retrieved from a previous authentication, used to retrieve a
        subsequent access token. If not provided (i.e. on the initial authentication), the password is used.
    """

    if url is None:
        url = auth_url

    if not current_refresh_token:  # First time through, send password
        data = {'username': user, 'password': password, 'client_id': clientid, 'grant_type': 'password', 'takeExclusiveSignOnControl': True,
                'scope': scope}
        print('Sending authentication request with password to {} ...'.format(url))
        #print(data)
    else:  # Use the given refresh token
        data = {'username': user, 'client_id': clientid, 'refresh_token': current_refresh_token, 'grant_type': 'refresh_token'}
        print("Sending authentication request with refresh token to {} ... ".format(url))
    if client_secret != '':
        data['client_secret'] = client_secret;
        
    try:
        # Request with auth for https protocol    
        r = requests.post(url,
                          headers={'Accept': 'application/json'},
                          data=data,
                          auth=(clientid, client_secret),
                          verify=True,
                          allow_redirects=False)

    except requests.exceptions.RequestException as e:
        print('Refinitiv Data Platform authentication exception failure:', e)
        return None, None, None

    if r.status_code == 200:
        auth_json = r.json()
        print('Refinitiv Data Platform Authentication succeeded. RECEIVED:')
        print(json.dumps(auth_json, sort_keys=True, indent=2, separators=(',', ':')))

        return auth_json['access_token'], auth_json['refresh_token'], auth_json['expires_in']
    elif r.status_code == 301 or r.status_code == 302 or r.status_code == 307 or r.status_code == 308:
        # Perform URL redirect
        print('Refinitiv Data Platform authentication HTTP code:', r.status_code, r.reason)
        new_host = r.headers['Location']
        if new_host is not None:
            print('Perform URL redirect to ', new_host)
            return get_sts_token(current_refresh_token, new_host)
        return None, None, None
    elif r.status_code == 400 or r.status_code == 401:
        # Retry with username and password
        print('Refinitiv Data Platform authentication HTTP code:', r.status_code, r.reason)
        if current_refresh_token:
            # Refresh token may have expired. Try using our password.
            print('Retry with username and password')
            return get_sts_token(None)
        return None, None, None
    elif r.status_code == 403 or r.status_code == 451:
        # Stop retrying with the request
        print('Refinitiv Data Platform authentication HTTP code:', r.status_code, r.reason)
        print('Stop retrying with the request')
        return None, None, None
    else:
        # Retry the request to Refinitiv Data Platform 
        print('Refinitiv Data Platform authentication HTTP code:', r.status_code, r.reason)
        print('Retry the request to Refinitiv Data Platform')
        return get_sts_token(current_refresh_token)

#### RDP Service Discovery

Once authentication is successful, you can request the list of RTO WebSocket endpoints from the RDP Service Discovery.

In [13]:
def query_service_discovery(url=None):

    if url is None:
        url = discovery_url

    print("Sending Refinitiv Data Platform service discovery request to " + url)

    try:
        r = requests.get(url, headers={"Authorization": "Bearer " + sts_token}, params={"transport": "websocket"}, allow_redirects=False)

    except requests.exceptions.RequestException as e:
        print('Refinitiv Data Platform service discovery exception failure:', e)
        return False

    if r.status_code == 200:
        # Authentication was successful. Deserialize the response.
        response_json = r.json()
        print("Refinitiv Data Platform Service discovery succeeded. RECEIVED:")
        print(json.dumps(response_json, sort_keys=True, indent=2, separators=(',', ':')))

        for index in range(len(response_json['services'])):
            if not response_json['services'][index]['location'][0].startswith(region):
                continue

            if len(response_json['services'][index]['location']) == 1:
                hostList.append(response_json['services'][index]['endpoint'] + ":" +str(response_json['services'][index]['port']))


        if len(hostList) == 0:
            print("The region:", region, "is not present in list of endpoints")
            sys.exit(1)

        return True

    elif r.status_code == 301 or r.status_code == 302 or r.status_code == 303 or r.status_code == 307 or r.status_code == 308:
        # Perform URL redirect
        print('Refinitiv Data Platform service discovery HTTP code:', r.status_code, r.reason)
        new_host = r.headers['Location']
        if new_host is not None:
            print('Perform URL redirect to ', new_host)
            return query_service_discovery(new_host)
        return False
    elif r.status_code == 403 or r.status_code == 451:
        # Stop trying with the request
        print('Refinitiv Data Platform service discovery HTTP code:', r.status_code, r.reason)
        print('Stop trying with the request')
        return False
    else:
        # Retry the service discovery request
        print('Refinitiv Data Platform service discovery HTTP code:', r.status_code, r.reason)
        print('Retry the service discovery request')
        return query_service_discovery()

### MRN Process Code

The MRN data can be subscribed with the *NewsTextAnalytics* domain and MRN-specific RIC name as following:
- *MRN_TRNA*: News Analytics: Company and C&E assets
- *MRN_TRNA_DOC*: News Analytics: Macroeconomic News & events
- *MRN_STORY*: Real-time News
- *MRN_TRSI*: News Sentiment Indices

In [14]:
# MRN variables

mrn_domain = 'NewsTextAnalytics'
mrn_item = 'MRN_STORY'

def send_mrn_request(ws):
    """ Create and send MRN request """
    mrn_req_json = {
        'ID': 2,
        "Domain": mrn_domain,
        'Key': {
            'Name': mrn_item,
            'Service': service
        }
    }

    ws.send(json.dumps(mrn_req_json))
    print("SENT:")
    print(json.dumps(mrn_req_json, sort_keys=True, indent=2, separators=(',', ':')))

### Initial Refresh Message
The Initial Refresh response does not contain any NTA data, all the fields related to news item and fragment are empty or 0. It contains only the relevant feed related or other static Fields. 

The application can just print out each incoming field data in a console for informational purpose or just ignore it.

In [15]:
# Process FieldList, Refresh and Status messages.

def decodeFieldList(fieldList_dict):
    for key, value in fieldList_dict.items():
        print("Name = %s: Value = %s" % (key, value))

def processRefresh(ws, message_json):

    print("RECEIVED: Refresh Message")
    decodeFieldList(message_json["Fields"])

def processStatus(ws, message_json):  # process incoming status message
    print("RECEIVED: Status Message")
    print(json.dumps(message_json, sort_keys=True, indent=2, separators=(',', ':')))

### MRN News Update messages Process Code

The updates contain only fields related to the item and the fragment. They do not contain any of the static or per-feed fields. The updates are not cached or conflated.

#### First Update
The first update contains all the fields related to the item and the first fragment, subsequent updates only contain the fields relating to the fragment they contain. The FRAG_NUM FID is set to 1 for the first Update of each item and is incremented in each subsequent Update for that item. This allows you to you to detect a missing fragment (and ensure correct order of the fragments for re-assembly). 


#### Subsequent Update and Multi Fragment Items
The subsequent update contains the fields necessary to identify the MRN data item, the order of this fragment among all the fragments for this item, and the fragment itself. The other point to note is that (for a Multi fragment item), Update messages with FRAG_NUM >1 will have fewer FIDs as the metadata is included in the first Update message (FRAG_NUM=1) for that item

#### News Fragments simple handle logic


<img src="images/mrn_flow_reconstruct.png"/>

In [16]:
def processMRNUpdate(ws, message_json):  # process incoming News Update messages

    fields_data = message_json["Fields"]
    # Dump the FieldList first (for informational purposes)
    # decodeFieldList(message_json["Fields"])

    # declare variables
    tot_size = 0
    guid = None

    try:
        # Get data for all requried fields
        fragment = base64.b64decode(fields_data["FRAGMENT"])
        frag_num = int(fields_data["FRAG_NUM"])
        guid = fields_data["GUID"]
        mrn_src = fields_data["MRN_SRC"]

        #print("GUID  = %s" % guid)
        #print("FRAG_NUM = %d" % frag_num)
        #print("MRN_SRC = %s" % mrn_src)

        if frag_num > 1:  # We are now processing more than one part of an envelope - retrieve the current details
            guid_index = next((index for (index, d) in enumerate(
                _news_envelopes) if d["guid"] == guid), None)
            envelop = _news_envelopes[guid_index]
            if envelop and envelop["data"]["mrn_src"] == mrn_src and frag_num == envelop["data"]["frag_num"] + 1:
                print("process multiple fragments for guid %s" %
                      envelop["guid"])

                #print("fragment before merge = %d" % len(envelop["data"]["fragment"]))

                # Merge incoming data to existing news envelop and getting FRAGMENT and TOT_SIZE data to local variables
                fragment = envelop["data"]["fragment"] = envelop["data"]["fragment"] + fragment
                envelop["data"]["frag_num"] = frag_num
                tot_size = envelop["data"]["tot_size"]
                print("TOT_SIZE = %d" % tot_size)
                print("Current FRAGMENT length = %d" % len(fragment))

                # The multiple fragments news are not completed, waiting.
                if tot_size != len(fragment):
                    return None
                # The multiple fragments news are completed, delete assoiclate GUID envelop
                elif tot_size == len(fragment):
                    del _news_envelopes[guid_index]
            else:
                print("Error: Cannot find fragment for GUID %s with matching FRAG_NUM or MRN_SRC %s" % (
                    guid, mrn_src))
                return None
        else:  # FRAG_NUM = 1 The first fragment
            tot_size = int(fields_data["TOT_SIZE"])
            print("FRAGMENT length = %d" % len(fragment))
            # The fragment news is not completed, waiting and add this news data to envelop object.
            if tot_size != len(fragment):
                print("Add new fragments to news envelop for guid %s" % guid)
                _news_envelopes.append({  # the envelop object is a Python dictionary with GUID as a key and other fields are data
                    "guid": guid,
                    "data": {
                        "fragment": fragment,
                        "mrn_src": mrn_src,
                        "frag_num": frag_num,
                        "tot_size": tot_size
                    }
                })
                return None

        # News Fragment(s) completed, decompress and print data as JSON to console
        if tot_size == len(fragment):
            print("decompress News FRAGMENT(s) for GUID  %s" % guid)
            decompressed_data = zlib.decompress(fragment, zlib.MAX_WBITS | 32)
            
            json_news = json.loads(decompressed_data)
            _news_messages.append(json_news)
            print("News = %s" % json_news)

    except KeyError as keyerror:
        print('KeyError exception: ', keyerror)
    except IndexError as indexerror:
        print('IndexError exception: ', indexerror)
    except binascii.Error as b64error:
        print('base64 decoding exception:', b64error)
    except zlib.error as error:
        print('zlib decompressing exception: ', error)
    # Some console environments like Windows may encounter this unicode display as a limitation of OS
    except UnicodeEncodeError as encodeerror:
        print("UnicodeEncodeError exception. Cannot decode unicode character for %s in this enviroment: " %
              guid, encodeerror)
    except Exception as e:
        print('exception: ', sys.exc_info()[0])

### JSON-OMM Process functions

In [17]:
def process_message(ws, message_json):
    """ Parse at high level and output JSON of message """
    message_type = message_json['Type']

    if message_type == "Refresh":
        if "Domain" in message_json:
            message_domain = message_json["Domain"]
            if message_domain == "Login":
                process_login_response(ws, message_json)
            elif message_domain:
                processRefresh(ws, message_json)
    elif message_type == "Update":
        if "Domain" in message_json and message_json["Domain"] == mrn_domain:
            processMRNUpdate(ws, message_json)
    elif message_type == "Status":
        processStatus(ws, message_json)
    elif message_type == "Ping":
        pong_json = {'Type': 'Pong'}
        ws.send(json.dumps(pong_json))
        print("SENT:")
        print(json.dumps(pong_json, sort_keys=True,
                         indent=2, separators=(',', ':')))


def process_login_response(ws, message_json):
    """ Send item request """
    send_mrn_request(ws)


def send_login_request(ws ,auth_token, is_refresh_token):
    """ Generate a login request from command line data (or defaults) and send """
    login_json = {
        'ID': 1,
        "Domain": 'Login',
        'Key': {
            'NameType': 'AuthnToken',
            'Elements': {
                'ApplicationId': '',
                'Position': '',
                'AuthenticationToken': ''
            }
        }
    }

    login_json['Key']['Name'] = user
    login_json['Key']['Elements']['ApplicationId'] = app_id
    login_json['Key']['Elements']['Position'] = position
    login_json['Key']['Elements']['AuthenticationToken'] = auth_token
    
    if is_refresh_token:
        login_json['Refresh'] = False

    ws.send(json.dumps(login_json))
    print("SENT:")
    print(json.dumps(login_json, sort_keys=True, indent=2, separators=(',', ':')))

def send_refresh_token(ws):
    print('Refreshing the access token')
    send_login_request(ws, sts_token, True)

def ws_disconnect(ws):
    print('Closing the WebSocket connection')
    if web_socket_open:
        ws.close()

### WebSocket Process functions

The code runs for 25~ minutes before stop the connection. You can change it to run forever by changing from the ```while time.time() < t_end:``` statement to ```while True:``` statment.

In [18]:
def on_message(ws, message):
    """ Called when message received, parse message into JSON for processing """
    print("RECEIVED: ")
    message_json = json.loads(message)
    # Uncomment to print RAW JSON message from the server
    #print(json.dumps(message_json, sort_keys=True, indent=2, separators=(',', ':')))

    for singleMsg in message_json:
        process_message(ws, singleMsg)
        
def on_error(ws, error):
    """ Called when websocket error has occurred """
    print(error)
    
def on_close(ws, close_status_code, close_msg):
    """ Called when websocket is closed """
    global web_socket_open
    print("WebSocket Closed")
    web_socket_open = False
    
def on_open(ws):
    """ Called when handshake is complete and websocket is open, send login """

    print("WebSocket successfully connected!")
    global web_socket_open
    web_socket_open = True
    send_login_request(ws,sts_token, refresh_token)
    

## Main Function 

if __name__ == "__main__":
    # RTO - RDP Login
    #print(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'))
    sts_token, refresh_token, expire_time = get_sts_token(None)
    if not sts_token:
        exit

    original_expire_time = expire_time

    # Query VIPs from Refinitiv Data Platform service discovery
    if not query_service_discovery():
        print('Failed to retrieve endpoints from Refinitiv Data Platform Service Discovery. Exiting...')
        exit
    #print(hostList[0])
    # Start websocket handshake
    ws_address = "wss://{}/WebSocket".format(hostList[0])
    print("Connecting to WebSocket " + ws_address + " ...")
    web_socket_app = websocket.WebSocketApp(ws_address, header=['User-Agent: Python'],
                                            on_message=on_message,
                                            on_error=on_error,
                                            on_close=on_close,
                                            subprotocols=['tr_json2'])
    web_socket_app.on_open = on_open
    
    #web_socket_app.keep_running = False

    # Event loop
    #wst = threading.Thread(target=web_socket_app.run_forever)
    wst = threading.Thread(target=web_socket_app.run_forever, kwargs={'sslopt': {'check_hostname': False}})
    wst.start()

    #time.sleep(90)
    #web_socket_app.close()
    t_end = time.time() + (60 * 10) # Running for 25~ Minutes
    try:
        #while True: # Change to this line for running forever
        while time.time() < t_end: # Running for 25~ Minutes
            #  Continue using current token until 90% of initial time before it expires.
            time.sleep(int(float(expire_time) * 0.90))

            sts_token, refresh_token, expire_time = get_sts_token(refresh_token)
            if not sts_token:
                exit

            if int(expire_time) != int(original_expire_time):
               print('expire time changed from {} sec to {} sec; retry with password'.format(str(original_expire_time), str(expire_time)))
               sts_token, refresh_token, expire_time = get_sts_token(None)
               if not sts_token:
                   exit 
               original_expire_time = expire_time

            # Update token.
            send_refresh_token(web_socket_app)
        else: # End time
            print('Close connection')
            ws_disconnect(web_socket_app)
            #print(datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S'))

    except KeyboardInterrupt:
        pass

Sending authentication request with password to https://api.refinitiv.com/auth/oauth2/v1/token ...
Refinitiv Data Platform Authentication succeeded. RECEIVED:
{
  "access_token":"eyJ0eXAiOiJhdCtqd3QiLCJhbGciOiJSUzI1NiIsImtpZCI6ImJlcGpHV0dkOW44WU9VQ1NwX3M3SXlRMmlKMFkzeWRFaHo1VDJJVlNqWTgifQ.eyJkYXRhIjoie1wiY2lwaGVydGV4dFwiOlwidWtfQ2JGOFRQN0R6dTk1THVHSUxqWndUQlBtWV90aGpFbnBpOFlKV1RpTC15cWo2QkhBVjAxY3hBWkxrZ3NjZVlnbXBpdGtGdzNyUWlBOW1kV1k0LTZqc3Q2eERPQk9MM2RWRUpvMV9TQndxbjdqSzkwcml2WlJjeGl2aXVLSXM2bWY3TnpfSmthSExaM1VtRWN0Uld6RW1aSmdCc2RQTlp2X3ZyT2l3YkRMV0RTeEprMlZGUEtfVmJ2Rkt4MnIzRFZ1Z0ZpelhXVWQ5enEtakN5M2NLM09vTHh2ODd5RmxGR1JwMDhYRE8zOFotYnAwTXljRFBtRkhOZlk4cmFfUUpCVjNMbDFzdXlPamdpTFlmUk9QQ25jQktlR2p4dWtrU0ZmVmxBb29oeDBObFAxdDR2SXJVM01zemp1aVNFM1BJMllUN1FDQjBCXzNhWjViYlpLUHB0ZkIxNVJwbGVocGRHakdYUFV2Zm1HTjNZWDJVbElnXzJMSzFmSGxtREpEV1BRekRDRERWOFFDRDhwNjVBXCIsXCJpdlwiOlwiZWY5X3k3ZG5rd3ZFRllZd1wiLFwicHJvdGVjdGVkXCI6XCJleUpoYkdjaU9pSkJWMU5mUlU1RFgxTkVTMTlCTWpVMklpd2laVzVqSWpvaVFUSTFOa2REVFNJc0

### Real-time News Data Model
The news data appears as JSON in UTF-8 after decompression and assembly of the individual messages.
The Real-time News feed contains the headline, story body text, and associated metadata about the story as a simple group of named values.

Example JSON fields are following:
- ```firstCreated```: UTC timestamp for the first version of the story. Millisecond precision.
- ```headline```: The headline text of the news item.
- ```id```: Uniquely identifies the news item. This is the same value as the GUID in the OMM envelope.
- ```body```: The full body text of the news item (Story Body).

For more detail regarding MRN data model please visit [MRN Data Models and Elektron Implementation Guide](https://developers.refinitiv.com/elektron/elektron-sdk-java/docs?content=8736&type=documentation_item) page. If you want to compare MRN and the legacy N2_UBMS news data model, please visit [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.refinitiv.com/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).

In [19]:
print("first 10 headlines\n")
for news in _news_messages[:10]:
    if news["headline"]:
        print(news["headline"])

first 10 headlines

Change of Director's Interest Notices x 3-CHK.AX
CJ대한통운, "고객님, 내일 상품 주문 두배 증가 예상됩니다"
NORGE: FORBRUKERTILLIT -9,2 I DES (-0,5 I NOV) -OPINION  
SGA Societe Generale Acceptance NV - 由 SG Issuer 或 SGA Societe Generale Acceptance N.V. 發行之牛熊證的剩餘價值之估值通告
SGA Societe Generale Acceptance NV - 由 SG Issuer 或 SGA Societe Generale Acceptance N.V. 发行之牛熊证的剩余价值之估值通告
LA DORIA - Pubblicazione Rendiconto sintetico delle votazioni  Assemblea 16/12/2021/Publication of Summary report of the votes- Sahreholders' meeting 16/12/2021 <LDO.MI>
LA DORIA - Pubblicazione Rendiconto sintetico delle votazioni  Assemblea 16/12/2021/Publication of Summary report of the votes- Sahreholders' meeting 16/12/2021 <LDO.MI>
REG-AMUNDI ETF MSCI EUROPE AMUNDI ETF MSCI EUROPE: Net Asset Value(s)
NORGE: FORBRUKERTILLIT -9,2 I DES (-0,5 I NOV) -OPINION  
美 국무부 경제차관, 송도 삼성바이오로직스 방문


In [20]:
print("first 10 stories\n")
for news in _news_messages[:10]:
    if news["body"]:
        print(news["body"])

first 10 stories

                                                                                                              Appendix 3Y
                                                                                       Change of Director’s Interest Notice

                                                                                                                                   Rule 3.19A.2

                                                 Appendix 3Y
                             Change of Director’s Interest Notice
Information or documents not available now must be given to ASX as soon as available. Information and
documents given to ASX become ASX’s property and may be made public.
Introduced 30/9/2001.

Name of entity               COHIBA MINERALS LIMITED

ABN                         72 149 026 308

We (the entity) give ASX the following information under listing rule 3.19A.2 and as agent for the
director for the purposes of section 205G of the Corporations Act.

    

In [21]:
# #uncomment if you do not have pandas and numpy installed\n
# #Install pandas and numpy packages in a current Jupyter kernal\n

# !{sys.executable} -m pip install pandas
# !{sys.executable} -m pip install numpy

In [22]:
import pandas as pd

In [23]:
df_headlines = pd.DataFrame(_news_messages, columns = ["firstCreated","messageType","provider","language","headline"])

In [24]:
messageType = {
    0: "Unknow",
    1: "Alert",
    2: "First take",
    3: "Subsequent take",
    4: "Correction",
    5: "Corrected",
    6: "Update",
    7: "Deletion",
    8: "Drop due to expiry"
}

In [25]:
df_headlines["messageType"] = [messageType[value] for value in df_headlines["messageType"] if value in messageType ]

In [29]:
df_headlines.head(10)

firstCreated messageType provider language  \
0  2021-12-17T09:15:51.395Z  First take   NS:ASX       en   
1  2021-12-17T08:53:59.055Z      Update   NS:MKN       ko   
2  2021-12-17T09:15:52.648Z  First take   NS:TDF       no   
3  2021-12-17T09:15:53.256Z  First take  NS:HIIS       zh   
4  2021-12-17T09:15:53.264Z  First take  NS:HIIS       zh   
5  2021-12-17T09:15:53.311Z  First take   NS:BIA       it   
6  2021-12-17T09:15:53.318Z  First take   NS:BIA       it   
7  2021-12-17T09:15:53.719Z  First take   NS:DGP       en   
8  2021-12-17T09:15:53.782Z  First take   NS:TDF       no   
9  2021-12-17T09:15:53.765Z  First take   NS:MTD       ko   

                                            headline  
0   Change of Director's Interest Notices x 3-CHK.AX  
1                CJ대한통운, "고객님, 내일 상품 주문 두배 증가 예상됩니다"  
2  NORGE: FORBRUKERTILLIT -9,2 I DES (-0,5 I NOV)...  
3  SGA Societe Generale Acceptance NV - 由 SG Issu...  
4  SGA Societe Generale Acceptance NV - 由 SG Issu...  
5  LA DORIA - Pubblicazione Rendiconto sintetico ...  
6  LA DORIA - Pubblicazione Rendiconto sintetico ...  
7  REG-AMUNDI ETF MSCI EUROPE AMUNDI ETF MSCI EUR...  
8  NORGE: FORBRUKERTILLIT -9,2 I DES (-0,5 I NOV)...  
9                         美 국무부 경제차관, 송도 삼성바이오로직스 방문

In [30]:
df_story = pd.DataFrame(_news_messages, columns = ["headline","body"])

In [31]:
df_story

headline  \
0      Change of Director's Interest Notices x 3-CHK.AX   
1                   CJ대한통운, "고객님, 내일 상품 주문 두배 증가 예상됩니다"   
2     NORGE: FORBRUKERTILLIT -9,2 I DES (-0,5 I NOV)...   
3     SGA Societe Generale Acceptance NV - 由 SG Issu...   
4     SGA Societe Generale Acceptance NV - 由 SG Issu...   
...                                                 ...   
2082  KUTXABANK BOLSA EUROZONA, FI-Otros hechos rele...   
2083  Nemetschek SE - Nemetschek Group Announces Str...   
2084                *TOP NEWS* Australia & New Zealand    
2085                           《興櫃股》洋基工程承銷價180元 套利空間46％   
2086                           《兴柜股》洋基工程承销价180元 套利空间46％   

                                                   body  
0                                                   ...  
1     \n   CJ대한통운이 AI·빅데이터 기술을 통해 이커머스 풀필먼트 고객사에 상품의...  
2     \nOslo (TDN Direkt): Forbrukertilliten (CCI) f...  
3     由 SG Issuer 或 SGA Societe Generale Acceptance ...  
4     由 SG Issuer 或 SGA Societe Generale Acceptance ...  
...                                                 ...  
2082  Modificación hora de corte 24 y 31 de diciembr...  
2083  *           Combining reality capture and AI t...  
2084  > Pubs, parties push Australia's COVID-19 case...  
2085  【時報-台北電】洋基工程（6691）初次上市（IPO）普通股股票承銷案，採競價拍賣及公開\r...  
2086  【时报-台北电】洋基工程（6691）初次上市（IPO）普通股股票承销案，采竞价拍卖及公开\r...  

[2087 rows x 2 columns]

## References

For further details, please check out the following resources:
* [Real-Time Market Data APIs & Distribution page](https://developers.lseg.com/en/use-cases-catalog/refinitiv-real-time) on the [LSEG Developer Community](https://developers.lseg.com/) website.
* [WebSocket API page](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/refinitiv-websocket-api).
* [Developer Webinar Recording: Introduction to Electron WebSocket API](https://www.youtube.com/watch?v=CDKWMsIQfaw).
* [Introduction to Machine Readable News with WebSocket API](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).
* [Machine Readable News (MRN) & N2_UBMS Comparison and Migration Guide](https://developers.lseg.com/en/article-catalog/article/machine-readable-news-mrn-n2_ubms-comparison-and-migration-guide).
* [Introduction to Machine Readable News (MRN) with Enterprise Message API (EMA)](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-mrn-elektron-message-api-ema).
* [MRN Data Models and Real-Time SDK Implementation Guide](https://developers.lseg.com/en/api-catalog/refinitiv-real-time-opnsrc/rt-sdk-java/documentation#mrn-data-models-implementation-guide).
* [MRN WebSocket JavaScript example on GitHub](https://github.com/LSEG-API-Samples/Example.WebSocketAPI.Javascript.NewsMonitor).
* [MRN WebSocket C# NewsViewer example on GitHub](https://github.com/LSEG-API-Samples/Example.WebSocketAPI.CSharp.MRNWebSocketViewer).
* [Developer Article: Introduction to Machine Readable News with WebSocket API](https://developers.lseg.com/en/article-catalog/article/introduction-machine-readable-news-elektron-websocket-api-refinitiv).
* [LSEG-API-Samples/Example.WebSocketAPI.Python.MRN.RTO](https://github.com/LSEG-API-Samples/Example.WebSocketAPI.Python.MRN.RTO) GitHub Repository.

For any questions related to this example or WebSocket API, please use the Developer Community [Q&A Forum](https://community.developers.refinitiv.com/spaces/152/websocket-api.html).